In [ ]:
import pandas as pd
import numpy as np
%matplotlib notebook
import matplotlib.pyplot as plt

In [ ]:
def time_string_to_int(tstring):
    s = tstring.split(':')
    return 60 * int(s[0]) + int(s[1])

In [ ]:
# segments: info on the original segments, for the 'TR BALIAN' etablishment

segments = pd.read_csv('../data/segments_random_several_sectors.csv', sep=';', decimal=',')
etablissement = 'TR BALIAN'
segments = segments[segments.loc[:, 'ETABLISSEMENT'] == etablissement]
segments['DEPART_MINUTE'] = segments.loc[:, 'DEPART_HEURE'].apply(time_string_to_int)
segments.sort_values(['DEPART_MINUTE', 'SEGMENT'], inplace=True)
segments.reset_index(drop=True, inplace=True)
segments.head()

In [ ]:
# places: list of places of the segments
# place_to_idx: place name to index in the places array
# n_places: number of places

places = sorted(list({ row['DEPART_LIEU'] for _, row in segments.iterrows() }
                     | { row['FIN_LIEU'] for _, row in segments.iterrows() }))  
place_to_idx = {places[i]: i for i in range(len(places))}
places[:10]

In [ ]:
distances_df = pd.read_csv('../data/distances.csv', index_col=0, sep=',', decimal='.')
distances = - np.ones((n_places, n_places), np.float64)
col_positions = - np.ones((distances_df.shape[1], ), np.int32)
for i, name in enumerate(distances_df.columns):
    if name in place_to_idx:
        col_positions[i] = place_to_idx[name]
        
for name, row in distances_df.iterrows():
    if name in place_to_idx:
        i = place_to_idx[name]
        for idx, j in enumerate(col_positions):
            distances[i, j] = row.iloc[idx]
            distances[j, i] = row.iloc[idx]

distances[:4, :4]

In [ ]:
# drivers: list of services names by alphabetic order
# n_drivers: number of services
# driver_to_idx: function that maps a service name to an index in the drivers array

drivers = sorted([x for x in (
    set(segments.loc[:, 'LUNDI'].unique())
    | set(segments.loc[:, 'MARDI'].unique())
    | set(segments.loc[:, 'MERCREDI'].unique())
    | set(segments.loc[:, 'JEUDI'].unique())
    | set(segments.loc[:, 'VENDREDI'].unique())
    ) if isinstance(x, str)])
n_drivers = len(drivers)
driver_to_idx_set = { drivers[i]: i for i in range(n_drivers) }

def driver_to_idx(driver_name):
    if isinstance(driver_name, str):
        return driver_to_idx_set[driver_name]
    else:
        return -1

drivers[:10], len(drivers)

In [ ]:
# drivers_info: dataframe with info on each service, in the same order than the drivers array

drivers_info = pd.read_csv('../data/facteurc_services_improved_unique.csv', sep=';').sort_values('SERVICE').reset_index(drop=True)
assert(drivers_info.loc[:, 'SERVICE'].tolist() == drivers)
drivers_info.head()

In [ ]:
# segments_list: numeric info of each segment, using indexes in the previous arrays, and minutes from midnight
# for times, and sorted by start time, defining the segments indexes

segments_list = pd.DataFrame({
    'start-time': segments.loc[:, 'DEPART_HEURE'].apply(time_string_to_int),
    'stop-time': segments.loc[:, 'FIN_HEURE'].apply(time_string_to_int),
    'start-place': segments.loc[:, 'DEPART_LIEU'].apply(lambda s: place_to_idx[s]),
    'stop-place': segments.loc[:, 'FIN_LIEU'].apply(lambda s: place_to_idx[s]),
    'mon': segments.loc[:, 'LUNDI'].apply(driver_to_idx),
    'tue': segments.loc[:, 'MARDI'].apply(driver_to_idx),
    'wed': segments.loc[:, 'MERCREDI'].apply(driver_to_idx),
    'thu': segments.loc[:, 'JEUDI'].apply(driver_to_idx),
    'fri': segments.loc[:, 'VENDREDI'].apply(driver_to_idx),
    'passengers': segments.loc[:, 'NB_PASSAGERS']
})

In [ ]:
segments_list.dtypes

In [ ]:
segments_list.head()

In [ ]:
# days: list of days abreviations

days = ('mon', 'tue', 'wed', 'thu', 'fri')

In [ ]:
segments_list.loc[:, 'start-time'].min(), segments_list.loc[:, 'stop-time'].max()

In [ ]:
# services: for each day, the list of segment indexes for each service, by order of application (segments indexes)

services = {
    day: [
        segments_list.index[segments_list.loc[:, day] == i].tolist()
        for i in range(n_drivers)
    ]
    for day in days
}
services

In [ ]:
drivers[15]

In [ ]:
segments.loc[segments.loc[:, 'LUNDI'] == 'JOIGNY 04']

In [ ]:
bus_capacities = [63, 59, 47, 37, 34, 33, 22, 16, 9]

In [ ]:
def draw_driver_timeline(driver_idx, day, services_, segments_list_):
    driver_idx = 15
    day = 'mon'
    driver_day_segments = services_[day][driver_idx]
    driver_day_segments_times = segments_list_.loc[driver_day_segments, ['start-time', 'stop-time']] / 60.
    times = [
        (row['start-time'], row['stop-time'] - row['start-time'])
        for _, row in driver_day_segments_times.iterrows()
    ]

    fig, ax = plt.subplots()
    ax.broken_barh(times, (0.2, 0.6))
    ax.set_ylim(0, 1)
    ax.set_xlim(driver_day_segments_times['start-time'].min(), driver_day_segments_times['stop-time'].max())
    ax.set_xlabel('hour of the day')
    ax.grid(True)
    plt.show()

draw_driver_timeline(15, 'mon', services, segments_list)

In [ ]:
# grouping segments that are close together, constructing new arrays with the same structures, but with
# new "segments" that are in fact composed of several segments behind the hood

# grouped_segments: for each segment group, the list of segments composing it, defining a new "segment index"
# grouped_services: same as services, but with segments indexes beeing in grouped_segments instead of segments

max_time_to_group = 10
grouped_segments = []
id_to_grouped_idx = dict()

def add_segment_group(segments_group):
    group_id = '-'.join([str(segment_idx) for segment_idx in segments_group])
    if group_id in id_to_grouped_idx:
        return id_to_grouped_idx[group_id]
    else:
        group_idx = len(grouped_segments)
        grouped_segments.append(segments_group)
        id_to_grouped_idx[group_id] = group_idx
        return group_idx

grouped_services = dict()
for day in days:
    grouped_services[day] = []
    for driver_idx in range(n_drivers):
        new_service = []
        cur_service = services[day][driver_idx]
        i = 0
        while i < len(cur_service):
            cur_group = [cur_service[i]]
            while i < len(cur_service) - 1 and (segments_list.loc[cur_service[i + 1], 'start-time'] - segments_list.loc[cur_service[i], 'stop-time']) <= max_time_to_group:
                i += 1
                cur_group.append(cur_service[i])
            new_service.append(int(add_segment_group(cur_group)))
            i += 1
        grouped_services[day].append(new_service)

In [ ]:
# in this cell we reorder grouped_segments by start-time, and change grouped_services indexes accordingly

idx_new2old = sorted(np.arange(len(grouped_segments)), key=grouped_segments.__getitem__)
idx_old2new = np.argsort(idx_new2old)
grouped_segments = [grouped_segments[new_idx] for new_idx in idx_new2old]
for day in days:
    for i in range(n_drivers):
        grouped_services[day][i] = [int(idx_old2new[old_idx]) for old_idx in grouped_services[day][i]]

In [ ]:
grouped_services

In [ ]:
grouped_segments

In [ ]:
# grouped_segments_list: same as segments_list but with the new "segments"

grouped_segments_list = pd.DataFrame({
    'start-time': [segments_list.loc[cur_group[0], 'start-time'] for cur_group in grouped_segments],
    'stop-time': [segments_list.loc[cur_group[-1], 'stop-time'] for cur_group in grouped_segments],
    'start-place': [segments_list.loc[cur_group[0], 'start-place'] for cur_group in grouped_segments],
    'stop-place': [segments_list.loc[cur_group[-1], 'stop-place'] for cur_group in grouped_segments],
    'mon': [segments_list.loc[cur_group[0], 'mon'] for cur_group in grouped_segments],
    'tue': [segments_list.loc[cur_group[0], 'tue'] for cur_group in grouped_segments],
    'wed': [segments_list.loc[cur_group[0], 'wed'] for cur_group in grouped_segments],
    'thu': [segments_list.loc[cur_group[0], 'thu'] for cur_group in grouped_segments],
    'fri': [segments_list.loc[cur_group[0], 'fri'] for cur_group in grouped_segments],
    'passengers': [max(segments_list.loc[cur_segment_idx, 'passengers'] for cur_segment_idx in cur_group) for cur_group in grouped_segments]
})
grouped_segments_list.head()

In [ ]:
# this cell just checks that no error was introduced in the grouping and reordering

reconstructed_services = {
    day: [
        sum([grouped_segments[sidx] for sidx in grouped_services[day][i]], [])
        for i in range(n_drivers)
    ]
    for day in days
}
for day in days:
    for i in range(n_drivers):
        assert(reconstructed_services[day][i] == services[day][i])
    

In [ ]:
draw_driver_timeline(15, 'mon', grouped_services, grouped_segments_list)

In [ ]:
grouped_services['mon'][15]

In [ ]:
grouped_segments[33], grouped_segments[34], grouped_segments[35]

In [ ]:
services['mon'][15]

In [ ]:
grouped_segments_list.loc[33, 'start-time'], grouped_segments_list.loc[33, 'stop-time']

In [ ]:
segments_list.loc[14, 'start-time'], segments_list.loc[42, 'stop-time']

In [ ]:
driver_profile = []
everyday_services = []
for driver_idx in range(n_drivers):
    driver_segments = [ grouped_services[day][driver_idx] for day in days ]
    everyday_services.append(sorted(list(set.intersection(*[set(s) for s in driver_segments]))))
    explored = [False] * 5
    cur_profile = []
    for i in range(5):
        if explored[i]:
            continue
        cur_day = driver_segments[i]
        s = str(i + 1)
        for j in range(i + 1, 5):
            if explored[j]:
                continue
            if cur_day == driver_segments[j]:
                s += str(j + 1)
                explored[j] = True
        cur_profile.append(s)
    driver_profile.append('-'.join(cur_profile))
driver_profile
profiles = dict()
for profile in driver_profile:
    if profile in profiles:
        profiles[profile] += 1
    else:
        profiles[profile] = 1
profiles

In [ ]:
# n_segments: number of grouped_segments
# segment_overlaps[i, j]: True iff i and j overlap each other. Symmetric matrix
# segment_contains[i, j]: True iff i start before and ends after j.

n_segments = grouped_segments_list.shape[0]
segment_overlaps = np.zeros((n_segments, n_segments), np.bool)
segment_contains = np.zeros((n_segments, n_segments), np.bool)
for i in range(n_segments):
    start1, stop1 = grouped_segments_list.loc[i, ['start-time', 'stop-time']]
    for j in range(i + 1, n_segments):
        start2, stop2 = grouped_segments_list.loc[j, ['start-time', 'stop-time']]
        if start1 <= stop2 and start2 <= stop1:
            segment_overlaps[i, j] = True
            segment_overlaps[j, i] = True
            if start1 <= start2 and stop1 >= stop2:
                segment_contains[i, j] = True
            if start2 <= start1 and stop2 >= stop1:
                segment_contains[j, i] = True

In [ ]:
# we now only consider mondays
# segment_idx_to_driver: matching a segment to a service, and a position

day = 'mon'
day_services = grouped_services[day]
segment_idx_to_driver = - np.ones((n_segments, 2), np.int64)
for driver_idx in range(n_drivers):
    driver_segments = day_services[driver_idx]
    for i in range(len(driver_segments)):
        segment_idx = driver_segments[i]
        segment_idx_to_driver[segment_idx, :] = driver_idx, i

segment_idx_to_driver

In [ ]:
day_segments_idx = np.array([idx for idx in range(n_segments) if segment_idx_to_driver[idx, 0] > 0])
n_day_segments = day_segments_idx.shape[0]
day_segments_idx, n_day_segments

In [ ]:
segment_overlaps.sum() // 2

In [ ]:
segment_contains.sum()

In [ ]:
# overlaps: overlaps[segment_idx][driver_idx] = the list of segments in driver_idx segments
# that overlap with segment_idx
overlaps = []
for segment_idx in range(n_segments):
    cur_segment_overlaps = []
    if segment_idx_to_driver[segment_idx, 0] > 0:
        for driver_idx in range(n_drivers):
            cur_segment_overlaps.append([idx for idx in day_services[driver_idx] if segment_overlaps[segment_idx, idx]])
    overlaps.append(cur_segment_overlaps)
print(overlaps[4])

In [ ]:
# surroundings: [:,:,0] left-stop-time, [:,:,1] left-stop-place, [:,:,2] right-stop-time, [:,:,3] right-stop-place

minute_min, minute_max = segments_list.loc[:, 'start-time'].min(), segments_list.loc[:, 'stop-time'].max()
n = ((minute_max - minute_min) // 5) + 1

surroundings = - np.ones((n_drivers, n, 4), np.int32)

for driver_idx in range(n_drivers):
    driver_segments = day_services[driver_idx]
    starts = grouped_segments_list.loc[driver_segments, ['start-time', 'start-place']].values
    stops = grouped_segments_list.loc[driver_segments, ['stop-time', 'stop-place']].values
    m = len(driver_segments)
    if m == 0:
        continue
    a1 = ((stops[0, 0] - minute_min) // 5) + 1
    b1 = 0
    for i in range(m):
        a0 = a1
        a1 = n if i == m - 1 else ((stops[i + 1, 0] - minute_min) // 5) + 1
        b0 = b1
        b1 = (starts[i, 0] - minute_min) // 5
        surroundings[driver_idx, a0:a1, 0] = stops[i, 0]
        surroundings[driver_idx, a0:a1, 1] = stops[i, 1]
        surroundings[driver_idx, b0:b1, 2] = starts[i, 0]
        surroundings[driver_idx, b0:b1, 3] = starts[i, 1]


In [ ]:
# what must be updated at each step: overlaps, segment_idx_to_driver, day_services, surroundings, grouped_segments_list

def get_min_speed_from_segments(new_segment_idx, left_segment_idx, right_segment_idx):
    max_speed = 0.
    if left_segment_idx > 0:
        left_end_place, left_end_time = grouped_segments_list.loc[left_segment_idx, ['stop-place', 'stop-time']]
        new_start_place, new_start_time = grouped_segments_list.loc[new_segment_idx, ['start-place', 'start-time']]
        max_speed = distances[left_end_place, new_start_place] / (new_start_time - left_end_time)
    if right_segment_idx > 0:
        right_start_place, right_start_time = grouped_segments_list.loc[right_segment_idx, ['start-place', 'start-time']]
        new_stop_place, new_stop_time = grouped_segments_list.loc[new_segment_idx, ['stop-place', 'stop-time']]
        max_speed = max(distances[right_start_place, new_stop_place] / (right_start_time - new_stop_time), max_speed)
    return max_speed

# @param new_segment_idx the segment that we are going to insert in place of segment_idx
# @param driver_idx the driver on which we are working
# @param segment_idx the original segment we are going to remove
def get_left_and_right_min_speeds_from_initial_segment(new_segment_idx, driver_idx, segment_idx):
    dst_segments = day_services[driver_idx]
    position = segment_idx_to_driver[segment_idx, 1]
    left_segment_idx, right_segment_idx = -1, -1
    if position > 0:
        left_segment_idx = dst_segments[position - 1]
    if position < len(dst_segments) - 1:
        right_segment_idx = dst_segments[position + 1]
    return get_min_speed_from_segments(new_segment_idx, left_segment_idx, right_segment_idx)


def get_left_and_right_min_speeds_from_void(new_segment_idx, driver_idx):
    dst_segments = day_services[driver_idx]
    segment_start, segment_stop = grouped_segments_list.loc[new_segment_idx, ['start-time', 'stop-time']]
    start_times = grouped_segments_list.loc[dst_segments, 'start-time'].values
    stop_times = grouped_segments_list.loc[dst_segments, 'stop-time'].values
    if segment_start < stop_times[0]:
        left_segment_idx = -1
    elif segment_start >= stop_times[-1]:
        left_segment_idx = dst_segments[-1]
    else:
        left_segment_idx = dst_segments[np.argmax(stop_times > segment_start) - 1]
    if segment_stop <= start_times[0]:
        right_segment_idx = dst_segments[0]
    elif segment_stop > start_times[-1]:
        right_segment_idx = -1
    else:
        right_segment_idx = dst_segments[np.argmax(start_times > segment_stop)]
    return get_min_speed_from_segments(new_segment_idx, left_segment_idx, right_segment_idx)


In [ ]:
max_speed_limit_kmh = 70.
max_speed_limit = max_speed_limit_kmh / 60.  # km / min

# @param segment_idx: the segment we are moving
# @param driver_idx: the driver we want to give the segment to
# returns: possible, exchange with possible True iff the move is possible, exchange is None if it's only
# moving the segment, else the list of segments that we swap with
def get_swapping(segment_idx, driver_idx):
    # TODO move some of these variables deeper inside the ifs
    src_driver_idx = segment_idx_to_driver[segment_idx, 0]
    src_capacity = drivers_info.loc[src_driver_idx, 'VEHICULE_CAPACITE']
    src_passengers = grouped_segments_list.loc[segment_idx, 'passengers']
    dst_capacity = drivers_info.loc[driver_idx, 'VEHICULE_CAPACITE']
    if src_passengers > dst_capacity:
        return False, None
    else:
        dst_overlapping_segments = overlaps[segment_idx][driver_idx]
        if len(dst_overlapping_segments) == 0:
            # TODO check for distances with left and right segments
            # TODO it's a particular case because we don't have a place to start from, we can't call
            # get_left_and_right_min_speeds_from_initial_segment
            return True, None
        elif len(dst_overlapping_segments) == 1:
            # We have a unique destination segment overlapping with the source segment
            dst_segment_idx = dst_overlapping_segments[0]
            dst_passengers = grouped_segments_list.loc[dst_segment_idx, 'passengers']
            if (dst_passengers > src_capacity):
                # the destination segment is to big for the source driver
                return False, None
            else:
                if segment_contains[dst_segment_idx, segment_idx]:
                    # the segment we want to move is smaller and inside the destination segment
                    if segment_contains[segment_idx, dst_segment_idx]:
                        # The exact same timing
                        if segment_idx > dst_segment_idx:
                            # We avoid duplicate swapping
                            return False, None
                        else:
                            # TODO easy case, just check the distances in both sides
                            return True, None
                    else:
                        # Strictly contained
                        # We avoid duplicate swapping
                        return False, None
                elif segment_contains[segment_idx, dst_segment_idx]:
                    # the segment we want to move is strictly bigger and contains the destination segment
                    # TODO easy case, check for distances in the destination driver
                    return True, None
                else:
                    # neither of the two segments contain the other one, complex overlap
                    # TODO split to avoid duplicates
                    # TODO difficult case
                    return True, None
        else:
            # For the moment we reject multi-segment swapping
            return False, None

# TODO check for distances
        
get_left_and_right_min_speeds_from_void(58, 15)
